## Description
In this part of the project, we will use supervised learning algorithms, namely, Decision Trees/Random Forests, SVM, and Logistic Regression algorithms to predict disease type given gene expression data.

## Import Packages

In [1]:
import pandas as pd
import numpy as np
import math
from sklearn.tree import DecisionTreeClassifier # Import Decision Tree Classifier
from sklearn.tree import plot_tree
# from sklearn.tree.export import export_text
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split # Import train_test_split function
from sklearn import metrics #Import scikit-learn metrics module for accuracy calculation
from sklearn.model_selection import KFold # import KFold

In [2]:
#Settings
pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', 100)

## Load in Data (Run this cell only once - large file)

In [3]:
data = pd.read_csv("combinedNormalized.csv")
data

ENSG00000000003.13  ENSG00000000005.5  ENSG00000000419.11  \
0              2715.2490          1710.5652           1981.2572   
1              1572.9316            22.2585           3554.9950   
2              2788.3903            13.1767           1316.6554   
3              4838.6908            24.1550           1190.1840   
4              4978.2465             8.3615           1959.7338   
...                  ...                ...                 ...   
6719             52.8694             1.0367           1419.1819   
6720              0.0000             0.0000           2378.1717   
6721            885.9091             0.0000           3185.3644   
6722            737.3829             0.0000           1134.2618   
6723             11.9920             0.0000            427.2158   

      ENSG00000000457.12  ENSG00000000460.15  ENSG00000000938.11  \
0              1194.1682            465.3820             47.8917   
1               457.8884            657.1547            570.2407   
2               699.3782            185.4873           1155.4944   
3               883.8543            103.2078            126.2649   
4               652.1994            181.8633            401.3535   
...                  ...                 ...                 ...   
6719           1108.1851            534.9144          24377.9989   
6720           2148.7078           1605.2407           3155.1283   
6721            463.5823            343.0726             51.0266   
6722           1159.0668            651.6932            170.2520   
6723            155.8963              2.9980          22922.7488   

      ENSG00000000971.14  ENSG00000001036.12  ENSG00000001084.9  \
0               843.3097           3359.7041          1892.7617   
1               611.5779           7962.1713          1842.1531   
2              1013.5915           4967.6121          1831.5599   
3              2285.9438           4580.6712          3606.7845   
4              1652.4476           6934.8448          2492.7814   
...                  ...                 ...                ...   
6719            189.7080           1458.5748          4508.4163   
6720            549.5056            719.5907          1373.7640   
6721             64.0547           1697.9925           607.9768   
6722             20.2949           6520.3143          1455.5984   
6723            146.9023            703.0323           184.3773   

      ENSG00000001167.13  ENSG00000001460.16  ENSG00000001461.15  \
0              6350.8507            687.1412           2182.1939   
1              1203.0171            348.7160           1047.2078   
2              1448.4223            486.5239           1920.7560   
3              1334.0162            648.8918           3477.2257   
4              1613.7755           2122.7837           8123.2273   
...                  ...                 ...                 ...   
6719           3060.2081            270.5672           2549.1367   
6720           5456.8121            455.9085           3201.4237   
6721           5871.3192            146.5658           1434.1739   
6722           2778.1522            323.5916           2314.7510   
6723            493.1719             49.4671            227.8484   

      ENSG00000001497.15  ENSG00000001561.6  ENSG00000001617.10  \
0              4570.5303           679.8534           3435.7061   
1              3107.7058           238.4836           1343.9874   
2              2722.5069          1338.9544           9151.7180   
3              1987.2998          3550.7887           1492.1218   
4              3039.4165          2189.6759            524.6861   
...                  ...                ...                 ...   
6719           2693.2319          1824.5143             41.4662   
6720           4820.7543          2354.0176              5.0321   
6721           3670.6602          1048.7600              9.7711   
6722           2844.6746          4796.3716              3.3825   
6723            451.1998 

## Preprocessing

In [4]:
dataset = data.iloc[0:6728,1:60485]
dataset = dataset.rename(columns = {'Cancer': 'CancerType'})
dataset.loc[dataset.CancerType == 'Brease', 'CancerType'] = 'Breast'
dataset.loc[dataset.CancerType == 'Hema', 'CancerType'] = 'Blood'
dataset.loc[dataset.CancerType == 'Bronchus', 'CancerType'] = 'Lung'
dataset

ENSG00000000005.5  ENSG00000000419.11  ENSG00000000457.12  \
0             1710.5652           1981.2572           1194.1682   
1               22.2585           3554.9950            457.8884   
2               13.1767           1316.6554            699.3782   
3               24.1550           1190.1840            883.8543   
4                8.3615           1959.7338            652.1994   
...                 ...                 ...                 ...   
6719             1.0367           1419.1819           1108.1851   
6720             0.0000           2378.1717           2148.7078   
6721             0.0000           3185.3644            463.5823   
6722             0.0000           1134.2618           1159.0668   
6723             0.0000            427.2158            155.8963   

      ENSG00000000460.15  ENSG00000000938.11  ENSG00000000971.14  \
0               465.3820             47.8917            843.3097   
1               657.1547            570.2407            611.5779   
2               185.4873           1155.4944           1013.5915   
3               103.2078            126.2649           2285.9438   
4               181.8633            401.3535           1652.4476   
...                  ...                 ...                 ...   
6719            534.9144          24377.9989            189.7080   
6720           1605.2407           3155.1283            549.5056   
6721            343.0726             51.0266             64.0547   
6722            651.6932            170.2520             20.2949   
6723              2.9980          22922.7488            146.9023   

      ENSG00000001036.12  ENSG00000001084.9  ENSG00000001167.13  \
0              3359.7041          1892.7617           6350.8507   
1              7962.1713          1842.1531           1203.0171   
2              4967.6121          1831.5599           1448.4223   
3              4580.6712          3606.7845           1334.0162   
4              6934.8448          2492.7814           1613.7755   
...                  ...                ...                 ...   
6719           1458.5748          4508.4163           3060.2081   
6720            719.5907          1373.7640           5456.8121   
6721           1697.9925           607.9768           5871.3192   
6722           6520.3143          1455.5984           2778.1522   
6723            703.0323           184.3773            493.1719   

      ENSG00000001460.16  ENSG00000001461.15  ENSG00000001497.15  \
0               687.1412           2182.1939           4570.5303   
1               348.7160           1047.2078           3107.7058   
2               486.5239           1920.7560           2722.5069   
3               648.8918           3477.2257           1987.2998   
4              2122.7837           8123.2273           3039.4165   
...                  ...                 ...                 ...   
6719            270.5672           2549.1367           2693.2319   
6720            455.9085           3201.4237           4820.7543   
6721            146.5658           1434.1739           3670.6602   
6722            323.5916           2314.7510           2844.6746   
6723             49.4671            227.8484            451.1998   

      ENSG00000001561.6  ENSG00000001617.10  ENSG00000001626.13  \
0              679.8534           3435.7061              2.0822   
1              238.4836           1343.9874              1.0599   
2             1338.9544           9151.7180            136.8349   
3             3550.7887           1492.1218            443.5741   
4             2189.6759            524.6861            112.8807   
...                 ...                 ...                 ...   
6719          1824.5143             41.4662              3.1100   
6720          2354.0176              5.0321              3.0193   
6721          1048.7600              9.7711              0.0000   
6722          4796.3716              3.3825              4.5100   
6723          1197.7031  

In [5]:
check = dataset.iloc[:,58607]
check_np = check.to_numpy()
print(check)
print(np.unique(check_np))

0       Kidney
1       Kidney
2       Kidney
3       Kidney
4       Kidney
         ...  
6719     Blood
6720     Blood
6721     Blood
6722     Blood
6723     Blood
Name: CancerType, Length: 6724, dtype: object
['Blood' 'Breast' 'Kidney' 'Lung']


## Decision Tree Model

In [6]:
#Shuffle Dataset
dataset = dataset.sample(frac=1).reset_index(drop=True)
# Reading data & split into training and testing sets
X = dataset.drop(['CancerType'], 1)
#print(X)
y = dataset['CancerType']
#print(y)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.3, random_state=12345)

#Model Definition & Fitting
#clf = DecisionTreeClassifier()
clf = RandomForestClassifier(min_samples_leaf = 50, max_depth = 4)
clf = clf.fit(X_train, y_train)

# Predict based on the given features for the test set
y_pred = clf.predict(X_test)
y_pred_train = clf.predict(X_train)
#predictions_probability = clf.predict_proba(X_test)
print(y_pred)
print(y_test)

['Kidney' 'Blood' 'Blood' ... 'Kidney' 'Kidney' 'Blood']
1739    Kidney
6112     Blood
2803     Blood
953     Breast
4244    Breast
         ...  
5984     Blood
3871      Lung
4349    Kidney
6154    Kidney
3929     Blood
Name: CancerType, Length: 2018, dtype: object


## Decision Tree Metrics & Plots

In [7]:
print("Train Accuracy:",metrics.accuracy_score(y_train, y_pred_train))
print("Train Precision:",metrics.precision_score(y_train, y_pred_train, average='micro'))
print("Train Recall:",metrics.recall_score(y_train, y_pred_train, average='micro'))

print("Test Accuracy:",metrics.accuracy_score(y_test, y_pred))
print("Test Precision:",metrics.precision_score(y_test, y_pred, average='micro'))
print("Test Recall:",metrics.recall_score(y_test, y_pred, average='micro'))


Train Accuracy: 0.9961750956226094
Train Precision: 0.9961750956226094
Train Recall: 0.9961750956226094
Test Accuracy: 0.9955401387512388
Test Precision: 0.9955401387512388
Test Recall: 0.9955401387512388


## Filter Features

In [8]:
imp_vals = clf.feature_importances_
print('max:',np.max(imp_vals))
print('min:',np.min(imp_vals))
print('mean:',np.mean(imp_vals))
imp_arr = imp_vals > 0
num_imp = 0
for i in imp_arr:
    if i>0:
        num_imp+=1
        
print('number of important features',num_imp)
# with np.printoptions(threshold=np.inf):
#      print(imp_vals>0)
print('bool array shape: ',imp_arr.shape)
print('dataset shape: ',X.shape)
filt_X = X.loc[:, imp_arr]
filt_X

max: 0.015264434699933126
min: 0.0
mean: 1.7062808196973057e-05
number of important features 769
bool array shape:  (58607,)
dataset shape:  (6724, 58607)


ENSG00000003400.13  ENSG00000003436.13  ENSG00000004866.17  \
0               273.0067           1461.5095           2230.2389   
1             15166.7122            180.7471           3386.0666   
2              1214.5779           5500.1455           2184.8384   
3               855.4923            434.9517            745.4443   
4               911.8692            435.1631           2990.0587   
...                  ...                 ...                 ...   
6719           1479.1539           1287.9565           2727.1901   
6720           6556.4273             82.0940           3627.6679   
6721           1488.3376           7764.3197           1666.0495   
6722          20891.5605             39.1641           2804.7553   
6723            729.2187            162.0486            147.0441   

      ENSG00000005073.5  ENSG00000006747.13  ENSG00000007312.11  \
0             2671.5655            145.7404             84.1600   
1                0.0000              8.5561           6592.4557   
2               32.0416           8495.0364             56.0728   
3               14.4110            757.2352             53.7139   
4                3.1157            206.6765             97.6261   
...                 ...                 ...                 ...   
6719             0.0000              0.0000            689.1513   
6720             0.0000            327.2667           3974.9034   
6721             7.4047           1336.0131             94.1450   
6722             2.0084           1723.2224           5793.2808   
6723             3.0009            145.0435           2347.7042   

      ENSG00000008735.13  ENSG00000010379.14  ENSG00000011105.10  \
0               805.6776              7.1844           2565.8524   
1                32.0853             38.5023             26.7377   
2                47.0611          11432.8531           6141.9794   
3               216.1657              0.0000           3082.6546   
4              7561.8677              5.1929           6562.7582   
...                  ...                 ...                 ...   
6719             21.0107              1.0505              8.4043   
6720             48.8127             36.6095             35.5001   
6721             41.2546              4.2312           3068.7046   
6722            458.9234             51.2147              7.0295   
6723            124.0372             54.0162             74.0222   

      ENSG00000011201.9  ENSG00000015285.9  ENSG00000016402.11  \
0              140.6087           145.7404             18.4741   
1                0.0000           616.0374              0.0000   
2              124.1613           100.1301             61.0794   
3             1333.6772           273.8099           1388.7012   
4              571.2165           459.0503           1836.2014   
...                 ...                ...                 ...   
6719             0.0000          6824.2784              1.0505   
6720             3.3281          3028.6035              0.0000   
6721           474.9563           905.4847            422.0659   
6722             3.0126          5720.9777              0.0000   
6723            40.0120          1310.3931             39.0117   

      ENSG00000023892.10  ENSG00000030304.11  ENSG00000037965.5  \
0               496.7490              2.0527          1535.4061   
1             11814.8699              0.0000             0.0000   
2               137.1782             39.0507           108.1405   
3               529.2786              0.0000            69.4351   
4              1607.7148              8.3086           157.8635   
...                  ...                 ...                ...   
6719           5843.0783              0.0000             0.0000   
6720           6934.7254              0.0000             1.1094   
6721           2173.7980              2.1156           104.7231   
6722          11168.8106              9.0379             0.0000   
6723           1300.3901             

## Export Filtered Dataset

In [9]:
exportDataset = filt_X.copy()
exportDataset['CancerType'] = y
exportDataset
#exportDataset.to_csv(r'combinedFiltered.csv', index = False)

ENSG00000003400.13  ENSG00000003436.13  ENSG00000004866.17  \
0               273.0067           1461.5095           2230.2389   
1             15166.7122            180.7471           3386.0666   
2              1214.5779           5500.1455           2184.8384   
3               855.4923            434.9517            745.4443   
4               911.8692            435.1631           2990.0587   
...                  ...                 ...                 ...   
6719           1479.1539           1287.9565           2727.1901   
6720           6556.4273             82.0940           3627.6679   
6721           1488.3376           7764.3197           1666.0495   
6722          20891.5605             39.1641           2804.7553   
6723            729.2187            162.0486            147.0441   

      ENSG00000005073.5  ENSG00000006747.13  ENSG00000007312.11  \
0             2671.5655            145.7404             84.1600   
1                0.0000              8.5561           6592.4557   
2               32.0416           8495.0364             56.0728   
3               14.4110            757.2352             53.7139   
4                3.1157            206.6765             97.6261   
...                 ...                 ...                 ...   
6719             0.0000              0.0000            689.1513   
6720             0.0000            327.2667           3974.9034   
6721             7.4047           1336.0131             94.1450   
6722             2.0084           1723.2224           5793.2808   
6723             3.0009            145.0435           2347.7042   

      ENSG00000008735.13  ENSG00000010379.14  ENSG00000011105.10  \
0               805.6776              7.1844           2565.8524   
1                32.0853             38.5023             26.7377   
2                47.0611          11432.8531           6141.9794   
3               216.1657              0.0000           3082.6546   
4              7561.8677              5.1929           6562.7582   
...                  ...                 ...                 ...   
6719             21.0107              1.0505              8.4043   
6720             48.8127             36.6095             35.5001   
6721             41.2546              4.2312           3068.7046   
6722            458.9234             51.2147              7.0295   
6723            124.0372             54.0162             74.0222   

      ENSG00000011201.9  ENSG00000015285.9  ENSG00000016402.11  \
0              140.6087           145.7404             18.4741   
1                0.0000           616.0374              0.0000   
2              124.1613           100.1301             61.0794   
3             1333.6772           273.8099           1388.7012   
4              571.2165           459.0503           1836.2014   
...                 ...                ...                 ...   
6719             0.0000          6824.2784              1.0505   
6720             3.3281          3028.6035              0.0000   
6721           474.9563           905.4847            422.0659   
6722             3.0126          5720.9777              0.0000   
6723            40.0120          1310.3931             39.0117   

      ENSG00000023892.10  ENSG00000030304.11  ENSG00000037965.5  \
0               496.7490              2.0527          1535.4061   
1             11814.8699              0.0000             0.0000   
2               137.1782             39.0507           108.1405   
3               529.2786              0.0000            69.4351   
4              1607.7148              8.3086           157.8635   
...                  ...                 ...                ...   
6719           5843.0783              0.0000             0.0000   
6720           6934.7254              0.0000             1.1094   
6721           2173.7980              2.1156           104.7231   
6722          11168.8106              9.0379             0.0000   
6723           1300.3901             

## Decision Tree Model of Filtered Dataset

In [10]:
#Model Definition & Fitting
#clf = DecisionTreeClassifier(min_samples_leaf = 5, max_depth = 20, criterion = 'gini')
clf = RandomForestClassifier(bootstrap = True, n_estimators = 200, min_samples_leaf = 10, max_depth = 10, criterion = 'entropy')

#Cross Validation
n_folds = 4
kf = KFold(n_splits=n_folds, random_state = 54321, shuffle = True)

#Split Train/CV from Test
X_train, X_test, y_train, y_test = train_test_split(filt_X, y, test_size = 0.3, random_state=12345)

train_acc_arr = np.array([])
test_acc_arr = np.array([])
for i, (train_index, cv_index) in enumerate(kf.split(X_train)):
    X_train, X_cv = filt_X.iloc[train_index], filt_X.iloc[cv_index]
    y_train, y_cv = y.iloc[train_index], y.iloc[cv_index]
    clf = clf.fit(X_train, y_train)

    # Predict based on the given features for the test set
    y_pred_cv = clf.predict(X_cv)
    y_pred_train = clf.predict(X_train)
    #predictions_probability = clf.predict_proba(X_test)
    print('Fold #: ', i)
    print("Train Accuracy:",metrics.accuracy_score(y_train, y_pred_train))
    train_acc_arr = np.append(train_acc_arr,metrics.accuracy_score(y_train, y_pred_train))
    print("CV Accuracy:",metrics.accuracy_score(y_cv, y_pred_cv))
    test_acc_arr = np.append(test_acc_arr,metrics.accuracy_score(y_cv, y_pred_cv))
print("Avg Train Accuracy:",np.mean(train_acc_arr))
print("Avg CV Accuracy:",np.mean(test_acc_arr))

y_pred_test = clf.predict(X_test)
print("Test Accuracy:",metrics.accuracy_score(y_test, y_pred_test))
print('---Test Data---')
y_test

Fold #:  0
Train Accuracy: 0.9985831680362709
CV Accuracy: 0.9949022939677146
Fold #:  1
Train Accuracy: 0.9991499008217626
CV Accuracy: 0.9974511469838573
Fold #:  2
Train Accuracy: 0.9988668555240793
CV Accuracy: 0.9965986394557823
Fold #:  3
Train Accuracy: 0.998300283286119
CV Accuracy: 0.9982993197278912
Avg Train Accuracy: 0.998725051917058
Avg CV Accuracy: 0.9968128500338113
Test Accuracy: 0.998017839444995
---Test Data---


1739    Kidney
6112     Blood
2803     Blood
953     Breast
4244    Breast
         ...  
5984     Blood
3871      Lung
4349    Kidney
6154    Kidney
3929     Blood
Name: CancerType, Length: 2018, dtype: object

## Visualize Tree

In [11]:
estimator = clf.estimators_[3]

classes = np.unique(y.to_numpy())
features = filt_X.columns

from sklearn.tree import export_graphviz
# Export as dot file
export_graphviz(estimator, out_file='tree.dot', 
                feature_names = features,
                class_names = classes,
                rounded = True, proportion = False, 
                precision = 2, filled = True)

# Convert to png using system command (requires Graphviz)
from subprocess import call
call(['dot', '-Tpng', 'tree.dot', '-o', 'tree.png', '-Gdpi=600'])

# Display in jupyter notebook
from IPython.display import Image
Image(filename = 'tree.png')

## Most Important Features

In [12]:
num_feat = 5
np_arr = np.zeros((num_feat,4))
cancer_types = np.unique(y)
most_important_genes = pd.DataFrame(np_arr,columns = cancer_types)
most_expressed_genes = most_important_genes.copy()
print('Cancer Types: ',cancer_types)
most_important_genes

Cancer Types:  ['Blood' 'Breast' 'Kidney' 'Lung']


Blood  Breast  Kidney  Lung
0    0.0     0.0     0.0   0.0
1    0.0     0.0     0.0   0.0
2    0.0     0.0     0.0   0.0
3    0.0     0.0     0.0   0.0
4    0.0     0.0     0.0   0.0

In [14]:
# #Shuffle Dataset
# dataset = dataset.sample(frac=1).reset_index(drop=True)

# Reading data & split into training and testing sets
X = exportDataset.drop(['CancerType'], 1)
y = exportDataset['CancerType']
y_prime = y.copy()

for i, cancer in enumerate(cancer_types):
    y_prime.loc[y_prime != cancer] = '0'
    y_prime.loc[y_prime == cancer] = '1'
    
    #Training
    X_train, X_test, y_train, y_test = train_test_split(X, y_prime, test_size = 0.3, random_state=12345)
#     print(y_train)
#     print(X_train)
    clf = RandomForestClassifier(min_samples_leaf = 50, max_depth = 4)
    clf = clf.fit(X_train, y_train)
    
    #Feature Importance
    imp_vals = np.array(clf.feature_importances_)
    num_feat = 5
    largest_ind = (-imp_vals).argsort()[:num_feat]
    print('Cancer Type: ',cancer)
    largest_features = X.columns[largest_ind]
    print(largest_features)
    most_important_genes.iloc[:,i] = largest_features
    
most_important_genes

Cancer Type:  Blood
Index(['ENSG00000109846.6', 'ENSG00000114019.13', 'ENSG00000197702.10',
       'ENSG00000137693.12', 'ENSG00000176720.4'],
      dtype='object')
Cancer Type:  Breast
Index(['ENSG00000003400.13', 'ENSG00000196878.11', 'ENSG00000197043.12',
       'ENSG00000197077.11', 'ENSG00000197142.9'],
      dtype='object')
Cancer Type:  Kidney
Index(['ENSG00000003400.13', 'ENSG00000196878.11', 'ENSG00000197043.12',
       'ENSG00000197077.11', 'ENSG00000197142.9'],
      dtype='object')
Cancer Type:  Lung
Index(['ENSG00000003400.13', 'ENSG00000196878.11', 'ENSG00000197043.12',
       'ENSG00000197077.11', 'ENSG00000197142.9'],
      dtype='object')


Blood              Breast              Kidney  \
0   ENSG00000109846.6  ENSG00000003400.13  ENSG00000003400.13   
1  ENSG00000114019.13  ENSG00000196878.11  ENSG00000196878.11   
2  ENSG00000197702.10  ENSG00000197043.12  ENSG00000197043.12   
3  ENSG00000137693.12  ENSG00000197077.11  ENSG00000197077.11   
4   ENSG00000176720.4   ENSG00000197142.9   ENSG00000197142.9   

                 Lung  
0  ENSG00000003400.13  
1  ENSG00000196878.11  
2  ENSG00000197043.12  
3  ENSG00000197077.11  
4   ENSG00000197142.9

In [15]:
# #Shuffle Dataset
# dataset = dataset.sample(frac=1).reset_index(drop=True)

# Reading data & split into training and testing sets
X = exportDataset.drop(['CancerType'], 1)
y = exportDataset['CancerType']
y_prime = y.copy()
X_prime = X.copy()
for i, cancer in enumerate(cancer_types):
    X_partial = X_prime.loc[y_prime == cancer].reset_index()
    max_values = np.mean(np.array(X_partial), axis = 0)
    largest_ind = (-max_values).argsort()[:num_feat]
    print('Cancer Type: ',cancer)
    largest_features = X.columns[largest_ind]
    print(largest_features)
    most_expressed_genes.iloc[:,i] = largest_features
most_expressed_genes

Cancer Type:  Blood
Index(['ENSG00000130701.3', 'ENSG00000212242.1', 'ENSG00000168067.10',
       'ENSG00000169604.18', 'ENSG00000211955.2'],
      dtype='object')
Cancer Type:  Breast
Index(['ENSG00000115461.4', 'ENSG00000113296.13', 'ENSG00000111432.4',
       'ENSG00000115468.10', 'ENSG00000171533.10'],
      dtype='object')
Cancer Type:  Kidney
Index(['ENSG00000113296.13', 'ENSG00000142627.12', 'ENSG00000115461.4',
       'ENSG00000146950.11', 'ENSG00000143450.13'],
      dtype='object')
Cancer Type:  Lung
Index(['ENSG00000185630.17', 'ENSG00000115461.4', 'ENSG00000168675.17',
       'ENSG00000205929.8', 'ENSG00000158636.15'],
      dtype='object')


Blood              Breast              Kidney  \
0   ENSG00000130701.3   ENSG00000115461.4  ENSG00000113296.13   
1   ENSG00000212242.1  ENSG00000113296.13  ENSG00000142627.12   
2  ENSG00000168067.10   ENSG00000111432.4   ENSG00000115461.4   
3  ENSG00000169604.18  ENSG00000115468.10  ENSG00000146950.11   
4   ENSG00000211955.2  ENSG00000171533.10  ENSG00000143450.13   

                 Lung  
0  ENSG00000185630.17  
1   ENSG00000115461.4  
2  ENSG00000168675.17  
3   ENSG00000205929.8  
4  ENSG00000158636.15